In [1]:
import numpy as np
import pandas as pd
from scipy.ndimage import gaussian_filter
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [2]:
import os
from pathlib import Path

path_cwd=Path.cwd()
path_input=str(path_cwd)+'/Data_input/'

import sys

sys.path.append(str(path_cwd)+'/Functions')
import Functions.reading

In [3]:
from csv import DictReader, reader

with open(path_input+'inputfiles.csv', encoding='utf-8-sig') as read_obj:
    dict_reader = DictReader(read_obj)
    list_of_dict = list(dict_reader)

    name_=[[list_of_dict[i].pop(key) for i in range(len(list_of_dict))]for key in ["Filename","Tree","Start_date"]] #extract string columns: Filename,Tree, Date (if applicable) .pop(key):removes specified element from list or dict 

    res = [dict([key, float(value)] for key, value in dicts.items()) for dicts in list_of_dict]#this will make all values integers ONLY WORKS if all values in file are numerical
    
    inputfiles=[(name_[0][i],name_[1][i],name_[2][i],res[i]) for i in range(len(list_of_dict))] #list of tuples: [(name,tree,date,{Dict})]

In [4]:
PSY_cols=['Date','Time','Chamber Temperature','dT','Wet Bulb Depression','Corrected Water Potential','Intercept','Slope','EDBO','Correction for dT','Correction Factor','IBV','IBT','EPS Present','EPS Voltage','EPS Current','Diagnostic Comment','NA'] #There is a file with something in the 18th column so we create an extra column
timeseries= []

In [5]:
for i,(name,tree,ini_date,options) in enumerate(inputfiles):
    if options['Reading'] == 1:
        from Functions.reading import read_Df1
        PSY=read_Df1(path_input,PSY_cols,name)
    if options['Reading'] == 2:
        from Functions.reading import read_Df2
        PSY,name2=read_Df2(path_input,PSY_cols,name)

    PSY=PSY.loc[ini_date:]
    psy_=PSY.copy()

   #REMOVING PROBLEMATIC MEASUREMENTS
    #replace zeros with nan- exact zeros occur when peltier cooling goes to zero right away- could be a really dry chamber or a chamber with resin 
    psy_['Corrected Water Potential (MPa)'] = psy_['Corrected Water Potential (MPa)'].replace(0.00, np.nan)
    #replace with nan a NON-ZERO value that is between two consecutive zeros- random spikes when psychrometer is not working properly
    psy_['Corrected Water Potential (MPa)'] = psy_['Corrected Water Potential (MPa)'].mask((psy_['Corrected Water Potential (MPa)'] != 0) & (psy_['Corrected Water Potential (MPa)'].shift(1) == 0) & (psy_['Corrected Water Potential (MPa)'].shift(-1) == 0))
    #if difference between two consecutive rows is more than 1.2 MPa, replace with nan- sudden peaks in the data, the instruments do that but they seem to be outliers, 1.2 Mpa is a thrshold but could be less
    psy_['Corrected Water Potential (MPa)'] = psy_['Corrected Water Potential (MPa)'].mask(psy_['Corrected Water Potential (MPa)'].diff().abs() > 1.2)
    #replace with nan a value that is between two consecutive nans- remove the spikes not removed by the previous step
    psy_['Corrected Water Potential (MPa)'] = psy_['Corrected Water Potential (MPa)'].mask((psy_['Corrected Water Potential (MPa)'].isnull()) & (psy_['Corrected Water Potential (MPa)'].shift(1).isnull()) & (psy_['Corrected Water Potential (MPa)'].shift(-1).isnull()))
    #interpolate some missing values 2 hours max
    psy_['Corrected Water Potential (MPa)'] = psy_['Corrected Water Potential (MPa)'].interpolate(method='linear', limit_direction='both', limit=4)

    #GAUSSIAN FILTER
    wp=psy_['Corrected Water Potential (MPa)']
    smooth = pd.Series(gaussian_filter(wp,2)) #0.5
    smooth.index = wp.index
    
    #INTERPOLATION 
    #Do it depending on the time of the day because some instruments stop measuring during daytime and the 'daily' drops are not representative 
    psy_out = psy_.copy()
    psy_out['Corrected Water Potential (MPa)']=smooth.values
    nighttime_condition = (psy_out.index.hour > 22.0) | (psy_out.index.hour < 9.0)
    daytime_condition = ~nighttime_condition  
    psy_out.loc[nighttime_condition,'Corrected Water Potential (MPa)'] = psy_out.loc[nighttime_condition,'Corrected Water Potential (MPa)'].interpolate(method='linear', limit_direction='both', limit=4)#12)
    psy_out.loc[daytime_condition, 'Corrected Water Potential (MPa)'] = psy_out.loc[daytime_condition, 'Corrected Water Potential (MPa)'].interpolate(method='linear', limit_direction='both', limit=4)
    

    #OUTPUT FILES 
    #Paths
    path_cwd = str(Path.cwd())
    path_corrpsy = path_cwd + "/Data_output/"
    path_TS= str(Path.cwd().parents[2])
    path_analysis= path_TS + "/ANALYSIS/Input_files/" 

    #Output
    print(psy_out.columns)
    psy_out=psy_out.drop(columns=['Chamber Temperature (C)', 'dT (C)', 'Wet Bulb Depression'])
    nam=os.path.splitext(name)[0]
    if options['Output'] == 1:
        nam=os.path.splitext(name)[0]
        
    if options['Output'] == 2:
        nam=name2
    
    outfile= 'PSY' + "-" + tree + "-" + "2021_corrected" + ".csv"
    psy_out.to_csv(path_corrpsy + outfile, index = True) 
    psy_out.to_csv(path_analysis + outfile, index = True)

    
    fig = px.line()
    fig.add_scatter(x=PSY.index.to_series(), y=PSY['Corrected Water Potential (MPa)'],name='zeros Xylem water potential (MPa)') 
    fig.add_scatter(x=psy_.index.to_series(), y=psy_['Corrected Water Potential (MPa)'],name='Gaussian Xylem water potential (MPa)')
    fig.add_scatter(x=smooth.index.to_series(), y=smooth.values,name='Gaussian Xylem water potential (MPa)')
    fig.add_scatter(x=psy_out.index.to_series(), y=psy_out['Corrected Water Potential (MPa)'],name='interpolated Gaussian Xylem water potential (MPa)')
    print(tree)
    fig.show()

Index(['Chamber Temperature (C)', 'dT (C)', 'Wet Bulb Depression',
       'Corrected Water Potential (MPa)'],
      dtype='object')
DF49GT


Index(['Chamber Temperature (C)', 'dT (C)', 'Wet Bulb Depression',
       'Corrected Water Potential (MPa)'],
      dtype='object')
ES48GT


Index(['Chamber Temperature (C)', 'dT (C)', 'Wet Bulb Depression',
       'Corrected Water Potential (MPa)'],
      dtype='object')
DF21US


Index(['Chamber Temperature (C)', 'dT (C)', 'Wet Bulb Depression',
       'Corrected Water Potential (MPa)'],
      dtype='object')
ES50LS


Index(['Chamber Temperature (C)', 'dT (C)', 'Wet Bulb Depression',
       'Corrected Water Potential (MPa)'],
      dtype='object')
ES51US


Index(['Chamber Temperature (C)', 'dT (C)', 'Wet Bulb Depression',
       'Corrected Water Potential (MPa)'],
      dtype='object')
DF27US
